![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 12. <i>Key logging</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Badania nad komputerowym wspomaganiem tłumaczenia często prowadzone są przy użyciu metodologii testowania interfejsów użytkownika - UI/UX testing. Program typu CAT traktuje się wówczas jak każdy inny program komputerowy i przeprowadza testy wydajności i użyteczności.

Testy takie prowadzone są zawsze na użytkownikach końcowych, w tym przypadku - na tłumaczach. Podstawowym celem testów jest próba zaobserwowania faktycznego sposobu pracy tłumacza - które funkcje programu są przez niego wykorzystywane najczęściej, jakich innych narzędzi poza CAT-em używa on do swojej pracy, które funkcje programu działają zgodnie, a które niezgodnie z intuicją użytkownika oraz wiele innych czynników. Aby wszystkie te analizy były możliwe, konieczne jest zgromadzenie jak największej ilości danych dotyczących przebiegu testu.

Testy są przede wszystkim nagrywane. Nagrywany jest zarówno ekran komputera (screen capture), jak i sam użytkownik pracujący przy komputerze. To jednak nie wszystko - często stosuje się specjalne techniki eye-trackingu, które są w stanie określić, w który punk ekranu użytkownik aktualnie patrzy. Dane pozyskane w ten sposób używane są do analizy czasu znalezienia przez użytkownika potrzebnej mu funkcji oraz zidentyfikowania miejsc, gdzie tej funkcji poszukiwał. Można również wyznaczyć obszary ekranu, które często skupiają uwagę użytkownika. 

Dodatkowo stosuje się jeszcze jedną technikę, która jest szczególnie przydatna z punktu widzenia analizy procesu tłumaczenia. Wykonuje się pełny key logging, tj. zapisuje się każde uderzenie użytkownika w dowolny klawisz na klawiaturze wraz z precyzyjnym czasem tego uderzenia. Dane pozyskane w ten sposób pozwalają na przeprowadzenie szeregu interesujących analiz.

Zapoznajmy się najpierw z programem typu key logger:

`sudo pip3 install keyboard`

In [ ]:
import keyboard


def report_key(event):
    print(event)

keyboard.on_release(callback=report_key)
keyboard.wait()

UWAGA! Aby uruchomić powyższy kod na Linuxie konieczne są uprawnienia administratora (pytanie poza konkursem - dlaczego?)

### Ćwiczenie 1: Wykorzystując powyższy kod napisz keylogger, który zapisuje wszystkie uderzenia w klawisze do pliku. Format pliku jest dowolny, każdy wpis musi zawierać precyzyjną godzinę uderzenia oraz uderzony klawisz. Uruchom program i przepisz paragraf dowolnie wybranego tekstu.

In [ ]:
import keyboard


def report_key(event: keyboard.KeyboardEvent):
    file = open('test.txt', 'a')
    file.write(f'[{event.time}] {event.name}\n')
    file.close()


keyboard.on_release(callback=report_key)
keyboard.wait()

Celem powyższego ćwiczenia jest pozyskanie danych testowych. Dalsze analizy będziemy prowadzili już bez key loggera, starając się korzystać jedynie z danych zapisanych w pliku. Oczywiście, jeśli zajdzie taka konieczność, można w każdej chwili wygenerować sobie nowy plik.

### Ćwiczenie 2: Napisz program, który wyliczy średnią prędkość pisania. Wykryj, kiedy użytkownik zaczął pisać. Nie bierz pod uwagę przerw dłuższych niż 5 sekund. Podaj prędkość pisania w znakach na minutę oraz słowach na minutę.

In [1]:
def calculate_typing_speed():
    import re
    import numpy

    def parse(line_l: str) -> (float, str):
        res = re.findall(r'(\d+.\d+)|([a-zA-Z,.]+)', ''.join(line_l.split()))
        return float(res[0][0]), res[1][1]

    file = open('test.txt',  'r')
    time_per_word = []
    time_per_character = []
    local_time_per_word = []

    prev_char_timestamp = None
    for line in file:
        time, key = parse(line)
        if prev_char_timestamp is None or time - prev_char_timestamp > 5:
            prev_char_timestamp = time
            local_time_per_word = []
            continue
        elapsed = time - prev_char_timestamp
        time_per_character.append(elapsed)
        if key == 'space' or key == 'enter' or key == ',' or key == '.':
            if len(local_time_per_word) > 0:
                time_per_word.append(numpy.sum(local_time_per_word))
            local_time_per_word = []
            time_per_character.append(elapsed)
            prev_char_timestamp = time
            continue
        local_time_per_word.append(elapsed)
        prev_char_timestamp = time
    file.close()
    time_per_word.append(numpy.sum(local_time_per_word))
    
    return 60 / numpy.average(time_per_character), 60 / numpy.average(time_per_word)

Wróćmy teraz do procesu tłumaczenia. Analiza uderzeń klawiszy wykonanych podczas tłumaczenia pozwala wykryć dłuższe pauzy. Pauzy te najczęściej wskazują miejsca, w których tłumacz musi się głębiej zastanowić nad tłumaczeniem danego słowa lub frazy. Przerwę tę wykorzystuje na przykład na sprawdzenie tłumaczenia lub definicji w słowniku, przeglądanie wyników z pamięci tłumaczeń lub korzystanie z innych pomocy (eye-tracking mógłby w tym przypadku rozstrzygnąć, czym w istocie zajmuje się w tym momencie tłuamcz). Jest też możliwe, że tłumacz poświęca pauzę na tzw. cognitive pause-and-unload - rodzaj zamyślenia, pozwalający oczyścić myśli. Z punktu widzenia projektowania systemu wspomagającego tłumaczenie niezwykle istotna jest informacja, nad czym tłumacz musi się dłużej zastanowić. Minimalizacja liczby i czasu trwania takich przerw jest szansą na usprawnienie procesu tłumaczenia.

### Ćwiczenie 3: Napisz program do wykrywania przerw w pisaniu. Raportuj długość oraz miejsce wystąpienia przerwy podając 20-znakowy kontekst z każdej strony. Wykryj każdą przerwę dłuższą niż 3 sekundy, posortuj wyniki malejąco po długości przerwy.

In [2]:
def find_pauses():
    import re

    def parse(line_l: str) -> (float, str):
        res = re.findall(r'(\d+.\d+)|([a-zA-Z,.]+)', ''.join(line_l.split()))
        return float(res[0][0]), res[1][1]

    file = open('test.txt', 'r')
    stops = []
    stop_reporting_time = 1

    prev_char_timestamp = None
    lines = file.readlines()
    file.close()
    for i in range(len(lines)):
        time, key = parse(lines[i])
        if prev_char_timestamp is None:
            prev_char_timestamp = time
            continue
        elapsed = time - prev_char_timestamp
        if elapsed > stop_reporting_time:
            context_start = max(0, i - 20)
            context_end = min(len(lines), i + 20)
            context_before = ''
            context_after = ''
            for j in range(context_start, i):
                time_l, key_l = parse(lines[j])
                context_before += key_l
            for j in range(i, context_end):
                time_l, key_l = parse(lines[j])
                context_after += key_l
            stops.append((elapsed, (context_before, context_after)))
        prev_char_timestamp = time

    def stop_sort(record: tuple):
        return record[0]

    stops.sort(reverse=True, key=stop_sort)
    
    return stops